In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import * # StringType
from pyspark.sql import Window
import pandas as pd
blob_container = "w261-team28-container" # The name of your container created in https://portal.azure.com
storage_account = "team28" # The name of your Storage account created in https://portal.azure.com
secret_scope = "w261-team28-scope" # The name of the scope created in your local computer using the Databricks CLI
secret_key = "w261-team28-key" # The name of the secret key created in your local computer using the Databricks CLI 
blob_url = f"wasbs://{blob_container}@{storage_account}.blob.core.windows.net"
mount_path = "/mnt/mids-w261"
spark.conf.set(
  f"fs.azure.sas.{blob_container}.{storage_account}.blob.core.windows.net",
  dbutils.secrets.get(scope = secret_scope, key = secret_key)
)

display(dbutils.fs.ls(f"{mount_path}"))

path name size dbfs:/mnt/mids-w261/HW5/ HW5/ 0 dbfs:/mnt/mids-w261/datasets_final_project/ datasets_final_project/ 0

In [0]:
# Inspect the Mount's Final Project folder 
display(dbutils.fs.ls("/mnt/mids-w261/datasets_final_project"))

path name size dbfs:/mnt/mids-w261/datasets_final_project/airlines/ airlines/ 0 dbfs:/mnt/mids-w261/datasets_final_project/airlines_data/ airlines_data/ 0 dbfs:/mnt/mids-w261/datasets_final_project/parquet_airlines_data/ parquet_airlines_data/ 0 dbfs:/mnt/mids-w261/datasets_final_project/parquet_airlines_data_3m/ parquet_airlines_data_3m/ 0 dbfs:/mnt/mids-w261/datasets_final_project/parquet_airlines_data_6m/ parquet_airlines_data_6m/ 0 dbfs:/mnt/mids-w261/datasets_final_project/stations_data/ stations_data/ 0 dbfs:/mnt/mids-w261/datasets_final_project/weather_data/ weather_data/ 0 dbfs:/mnt/mids-w261/datasets_final_project/weather_data_6_hr/ weather_data_6_hr/ 0 dbfs:/mnt/mids-w261/datasets_final_project/weather_data_single/ weather_data_single/ 0

#### Loading weather data before July 1st, 2015

In [0]:
# Load the 2015 Q1 for Weather
df_weather = spark.read.parquet("/mnt/mids-w261/datasets_final_project/weather_data/*").filter(col('DATE') < "2015-07-01T00:00:00.000")
display(df_weather)

STATION DATE SOURCE LATITUDE LONGITUDE ELEVATION NAME REPORT_TYPE CALL_SIGN QUALITY_CONTROL WND CIG VIS TMP DEW SLP AW1 GA1 GA2 GA3 GA4 GE1 GF1 KA1 KA2 MA1 MD1 MW1 MW2 OC1 OD1 OD2 REM EQD AW2 AX4 GD1 AW5 GN1 AJ1 AW3 MK1 KA4 GG3 AN1 RH1 AU5 HL1 OB1 AT8 AW7 AZ1 CH1 RH3 GK1 IB1 AX1 CT1 AK1 CN2 OE1 MW5 AO1 KA3 AA3 CR1 CF2 KB2 GM1 AT5 AY2 MW6 MG1 AH6 AU2 GD2 AW4 MF1 AA1 AH2 AH3 OE3 AT6 AL2 AL3 AX5 IB2 AI3 CV3 WA1 GH1 KF1 CU2 CT3 SA1 AU1 KD2 AI5 GO1 GD3 CG3 AI1 AL1 AW6 MW4 AX6 CV1 ME1 KC2 CN1 UA1 GD5 UG2 AT3 AT4 GJ1 MV1 GA5 CT2 CG2 ED1 AE1 CO1 KE1 KB1 AI4 MW3 KG2 AA2 AX2 AY1 RH2 OE2 CU3 MH1 AM1 AU4 GA6 KG1 AU3 AT7 KD1 GL1 IA1 GG2 OD3 UG1 CB1 AI6 CI1 CV2 AZ2 AD1 AH1 WD1 AA4 KC1 IA2 CF3 AI2 AT1 GD4 AX3 AH4 KB3 CU1 CN4 AT2 CG1 CF1 GG1 MV2 CW1 GG4 AB1 AH5 CN3 3809099999 2015-01-01T00:00:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-12 99999 V020 200,1,N,0077,1 00240,1,C,N 008000,1,9,9 +0113,1 +0099,1 10306,1 01,1,+00180,1,07,1 05,1,+00240,1,07,1 08,1,+00360,1,07,1 9,AGL ,+99999,+99999 08,99,1,01,1,99,9,00180,1,99,9,99,9 99999,9,10213,1 3,1,002,1,+999,9 51,1 3,99,0144,1,999 4,99,0134,1,999 SYN10603809 11358 82015 10113 20099 30213 40306 53002 69901 75165 887// 333 81706 85708 88712 90710 91128 91026= 5,1,02,1 06,0000,2,1 6,1,02,1 3809099999 2015-01-01T00:50:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-15 99999 V020 210,1,N,0077,1 00183,1,C,N 008000,1,9,9 +0110,1 +0100,1 99999,9 02,1,+00122,1,99,9 04,1,+00183,1,99,9 08,1,+00305,1,99,9 9,AGL ,+99999,+99999 99,99,9,02,1,99,9,00122,1,99,9,99,9 10290,1,99999,9 51,1 MET079METAR EGDR 010050Z 21015KT 8000 -DZ FEW004 SCT006 OVC010 11/10 Q1029 YLO1= 3809099999 2015-01-01T01:00:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-12 99999 V020 210,1,N,0077,1 00300,1,9,N 008000,1,9,9 +0113,1 +0101,1 10300,1 01,1,+00120,1,07,1 03,1,+00180,1,07,1 08,1,+00300,1,07,1 9,AGL ,+99999,+99999 08,99,1,01,1,99,9,00120,1,99,9,99,9 99999,9,10206,1 8,1,004,1,+999,9 51,1 3,99,0134,1,999 SYN09403809 41258 82115 10113 20101 30206 40300 58004 75155 887// 333 81704 83706 88710 90710 91126= 5,1,02,1 5,1,02,1 3809099999 2015-01-01T01:50:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-15 99999 V020 200,1,N,0082,1 00244,1,9,N 008000,1,9,9 +0120,1 +0100,1 99999,9 04,1,+00183,1,99,9 07,1,+00244,1,99,9 08,1,+00305,1,99,9 9,AGL ,+99999,+99999 99,99,9,04,1,99,9,00183,1,99,9,99,9 10290,1,99999,9 05,1 0144,1 MET086METAR EGDR 010150Z 20016G28KT 8000 HZ SCT006 BKN008 OVC010 12/10 Q1029 REDZ YLO1= 3809099999 2015-01-01T02:00:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-12 99999 V020 200,1,N,0082,1 00240,1,C,N 008000,1,9,9 +0115,1 +0100,1 10294,1 03,1,+00180,1,07,1 05,1,+00240,1,07,1 08,1,+00300,1,07,1 9,AGL ,+99999,+99999 08,99,1,03,1,99,9,00180,1,99,9,99,9 99999,9,10201,1 8,1,008,1,+999,9 20,1 3,99,0149,1,999 4,99,0144,1,999 SYN10003809 41358 82016 10115 20100 30201 40294 58008 72052 886// 333 83706 85708 88710 90710 91129 91028= 2,1,02,1 5,1,02,1 3809099999 2015-01-01T02:50:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-15 99999 V020 210,1,N,0093,1 00122,1,9,N 006000,1,9,9 +0110,1 +0110,1 99999,9 02,1,+00061,1,99,9 07,1,+00122,1,99,9 08,1,+00213,1,99,9 9,AGL ,+99999,+99999 99,99,9,02,1,99,9,00061,1,99,9,99,9 10290,1,99999,9 51,1 MET079METAR EGDR 010250Z 21018KT 6000 -DZ FEW002 BKN004 OVC007 11/11 Q1029 YLO2= 3809099999 2015-01-01T03:00:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-12 99999 V020 210,1,N,0093,1 00120,1,C,N 006000,1,9,9 +0111,1 +0106,1 10296,1 01,1,+00060,1,07,1 05,1,+00120,1,07,1 08,1,+00210,1,07,1 9,AGL ,+99999,+99999 08,99,1,01,1,99,9,00060,1,99,9,99,9 99999,9,10203,1 5,1,010,1,+999,9 50,1 3,99,0144,1,999 SYN09403809 41156 82118 10111 20106 30203 40296 55010 75052 887// 333 81702 85704 88707 90710 91128= 2,1,02,1 5,1,02,1 3809099999 2015-01-01T03:50:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-15 99999 V020 200,1,N,0082,1 00122,1,9,N 006000,1,9,9 +0110,1 +0110,1 99999,9 02,1,+00061,1,99,9 07,1,+00122,1,99,9 08,1,+00183,1,99,9 9,AGL ,+99999,+

**Columns in the weather data dataframe**

In [0]:
sorted(df_weather.columns)

Out[8]: ['AA1',
 'AA2',
 'AA3',
 'AA4',
 'AB1',
 'AD1',
 'AE1',
 'AH1',
 'AH2',
 'AH3',
 'AH4',
 'AH5',
 'AH6',
 'AI1',
 'AI2',
 'AI3',
 'AI4',
 'AI5',
 'AI6',
 'AJ1',
 'AK1',
 'AL1',
 'AL2',
 'AL3',
 'AM1',
 'AN1',
 'AO1',
 'AT1',
 'AT2',
 'AT3',
 'AT4',
 'AT5',
 'AT6',
 'AT7',
 'AT8',
 'AU1',
 'AU2',
 'AU3',
 'AU4',
 'AU5',
 'AW1',
 'AW2',
 'AW3',
 'AW4',
 'AW5',
 'AW6',
 'AW7',
 'AX1',
 'AX2',
 'AX3',
 'AX4',
 'AX5',
 'AX6',
 'AY1',
 'AY2',
 'AZ1',
 'AZ2',
 'CALL_SIGN',
 'CB1',
 'CF1',
 'CF2',
 'CF3',
 'CG1',
 'CG2',
 'CG3',
 'CH1',
 'CI1',
 'CIG',
 'CN1',
 'CN2',
 'CN3',
 'CN4',
 'CO1',
 'CR1',
 'CT1',
 'CT2',
 'CT3',
 'CU1',
 'CU2',
 'CU3',
 'CV1',
 'CV2',
 'CV3',
 'CW1',
 'DATE',
 'DEW',
 'ED1',
 'ELEVATION',
 'EQD',
 'GA1',
 'GA2',
 'GA3',
 'GA4',
 'GA5',
 'GA6',
 'GD1',
 'GD2',
 'GD3',
 'GD4',
 'GD5',
 'GE1',
 'GF1',
 'GG1',
 'GG2',
 'GG3',
 'GG4',
 'GH1',
 'GJ1',
 'GK1',
 'GL1',
 'GM1',
 'GN1',
 'GO1',
 'HL1',
 'IA1',
 'IA2',
 'IB1',
 'IB2',
 'KA1',
 'KA2',
 'KA3',
 'KA4',
 'KB1',
 'KB2',
 'KB3',
 'KC1',
 'KC2',
 'KD1',
 'KD2',
 'KE1',
 'KF1',
 'KG1',
 'KG2',
 'LATITUDE',
 'LONGITUDE',
 'MA1',
 'MD1',
 'ME1',
 'MF1',
 'MG1',
 'MH1',
 'MK1',
 'MV1',
 'MV2',
 'MW1',
 'MW2',
 'MW3',
 'MW4',
 'MW5',
 'MW6',
 'NAME',
 'OB1',
 'OC1',
 'OD1',
 'OD2',
 'OD3',
 'OE1',
 'OE2',
 'OE3',
 'QUALITY_CONTROL',
 'REM',
 'REPORT_TYPE',
 'RH1',
 'RH2',
 'RH3',
 'SA1',
 'SLP',
 'SOURCE',
 'STATION',
 'TMP',
 'UA1',
 'UG1',
 'UG2',
 'VIS',
 'WA1',
 'WD1',
 'WND']

In [0]:
df_weather.printSchema()

root
-- STATION: string (nullable = true)
-- DATE: timestamp (nullable = true)
-- SOURCE: short (nullable = true)
-- LATITUDE: double (nullable = true)
-- LONGITUDE: double (nullable = true)
-- ELEVATION: double (nullable = true)
-- NAME: string (nullable = true)
-- REPORT_TYPE: string (nullable = true)
-- CALL_SIGN: string (nullable = true)
-- QUALITY_CONTROL: string (nullable = true)
-- WND: string (nullable = true)
-- CIG: string (nullable = true)
-- VIS: string (nullable = true)
-- TMP: string (nullable = true)
-- DEW: string (nullable = true)
-- SLP: string (nullable = true)
-- AW1: string (nullable = true)
-- GA1: string (nullable = true)
-- GA2: string (nullable = true)
-- GA3: string (nullable = true)
-- GA4: string (nullable = true)
-- GE1: string (nullable = true)
-- GF1: string (nullable = true)
-- KA1: string (nullable = true)
-- KA2: string (nullable = true)
-- MA1: string (nullable = true)
-- MD1: string (nullable = true)
-- MW1: string (nullable = true)
-- MW2: string (nullable = true)
-- OC1: string (nullable = true)
-- OD1: string (nullable = true)
-- OD2: string (nullable = true)
-- REM: string (nullable = true)
-- EQD: string (nullable = true)
-- AW2: string (nullable = true)
-- AX4: string (nullable = true)
-- GD1: string (nullable = true)
-- AW5: string (nullable = true)
-- GN1: string (nullable = true)
-- AJ1: string (nullable = true)
-- AW3: string (nullable = true)
-- MK1: string (nullable = true)
-- KA4: string (nullable = true)
-- GG3: string (nullable = true)
-- AN1: string (nullable = true)
-- RH1: string (nullable = true)
-- AU5: string (nullable = true)
-- HL1: string (nullable = true)
-- OB1: string (nullable = true)
-- AT8: string (nullable = true)
-- AW7: string (nullable = true)
-- AZ1: string (nullable = true)
-- CH1: string (nullable = true)
-- RH3: string (nullable = true)
-- GK1: string (nullable = true)
-- IB1: string (nullable = true)
-- AX1: string (nullable = true)
-- CT1: string (nullable = true)
-- AK1: string (nullable = true)
-- CN2: string (nullable = true)
-- OE1: string (nullable = true)
-- MW5: string (nullable = true)
-- AO1: string (nullable = true)
-- KA3: string (nullable = true)
-- AA3: string (nullable = true)
-- CR1: string (nullable = true)
-- CF2: string (nullable = true)
-- KB2: string (nullable = true)
-- GM1: string (nullable = true)
-- AT5: string (nullable = true)
-- AY2: string (nullable = true)
-- MW6: string (nullable = true)
-- MG1: string (nullable = true)
-- AH6: string (nullable = true)
-- AU2: string (nullable = true)
-- GD2: string (nullable = true)
-- AW4: string (nullable = true)
-- MF1: string (nullable = true)
-- AA1: string (nullable = true)
-- AH2: string (nullable = true)
-- AH3: string (nullable = true)
-- OE3: string (nullable = true)
-- AT6: string (nullable = true)
-- AL2: string (nullable = true)
-- AL3: string (nullable = true)
-- AX5: string (nullable = true)
-- IB2: string (nullable = true)
-- AI3: string (nullable = true)
-- CV3: string (nullable = true)
-- WA1: string (nullable = true)
-- GH1: string (nullable = true)
-- KF1: string (nullable = true)
-- CU2: string (nullable = true)
-- CT3: string (nullable = true)
-- SA1: string (nullable = true)
-- AU1: string (nullable = true)
-- KD2: string (nullable = true)
-- AI5: string (nullable = true)
-- GO1: string (nullable = true)
-- GD3: string (nullable = true)
-- CG3: string (nullable = true)
-- AI1: string (nullable = true)
-- AL1: string (nullable = true)
-- AW6: string (nullable = true)
-- MW4: string (nullable = true)
-- AX6: string (nullable = true)
-- CV1: string (nullable = true)
-- ME1: string (nullable = true)
-- KC2: string (nullable = true)
-- CN1: string (nullable = true)
-- UA1: string (nullable = true)
-- GD5: string (nullable = true)
-- UG2: string (nullable = true)
-- AT3: string (nullable = true)
-- AT4: string (nullable = true)
-- GJ1: string (nullable = true)
-- MV1: string (nullable = true)
-- GA5: string (nullable = true)
-- CT2: string (nullable = true)
-- CG2: string

In [0]:
df_weather.dtypes

Out[10]: [('STATION', 'string'),
 ('DATE', 'timestamp'),
 ('SOURCE', 'smallint'),
 ('LATITUDE', 'double'),
 ('LONGITUDE', 'double'),
 ('ELEVATION', 'double'),
 ('NAME', 'string'),
 ('REPORT_TYPE', 'string'),
 ('CALL_SIGN', 'string'),
 ('QUALITY_CONTROL', 'string'),
 ('WND', 'string'),
 ('CIG', 'string'),
 ('VIS', 'string'),
 ('TMP', 'string'),
 ('DEW', 'string'),
 ('SLP', 'string'),
 ('AW1', 'string'),
 ('GA1', 'string'),
 ('GA2', 'string'),
 ('GA3', 'string'),
 ('GA4', 'string'),
 ('GE1', 'string'),
 ('GF1', 'string'),
 ('KA1', 'string'),
 ('KA2', 'string'),
 ('MA1', 'string'),
 ('MD1', 'string'),
 ('MW1', 'string'),
 ('MW2', 'string'),
 ('OC1', 'string'),
 ('OD1', 'string'),
 ('OD2', 'string'),
 ('REM', 'string'),
 ('EQD', 'string'),
 ('AW2', 'string'),
 ('AX4', 'string'),
 ('GD1', 'string'),
 ('AW5', 'string'),
 ('GN1', 'string'),
 ('AJ1', 'string'),
 ('AW3', 'string'),
 ('MK1', 'string'),
 ('KA4', 'string'),
 ('GG3', 'string'),
 ('AN1', 'string'),
 ('RH1', 'string'),
 ('AU5', 'string'),
 ('HL1', 'string'),
 ('OB1', 'string'),
 ('AT8', 'string'),
 ('AW7', 'string'),
 ('AZ1', 'string'),
 ('CH1', 'string'),
 ('RH3', 'string'),
 ('GK1', 'string'),
 ('IB1', 'string'),
 ('AX1', 'string'),
 ('CT1', 'string'),
 ('AK1', 'string'),
 ('CN2', 'string'),
 ('OE1', 'string'),
 ('MW5', 'string'),
 ('AO1', 'string'),
 ('KA3', 'string'),
 ('AA3', 'string'),
 ('CR1', 'string'),
 ('CF2', 'string'),
 ('KB2', 'string'),
 ('GM1', 'string'),
 ('AT5', 'string'),
 ('AY2', 'string'),
 ('MW6', 'string'),
 ('MG1', 'string'),
 ('AH6', 'string'),
 ('AU2', 'string'),
 ('GD2', 'string'),
 ('AW4', 'string'),
 ('MF1', 'string'),
 ('AA1', 'string'),
 ('AH2', 'string'),
 ('AH3', 'string'),
 ('OE3', 'string'),
 ('AT6', 'string'),
 ('AL2', 'string'),
 ('AL3', 'string'),
 ('AX5', 'string'),
 ('IB2', 'string'),
 ('AI3', 'string'),
 ('CV3', 'string'),
 ('WA1', 'string'),
 ('GH1', 'string'),
 ('KF1', 'string'),
 ('CU2', 'string'),
 ('CT3', 'string'),
 ('SA1', 'string'),
 ('AU1', 'string'),
 ('KD2', 'string'),
 ('AI5', 'string'),
 ('GO1', 'string'),
 ('GD3', 'string'),
 ('CG3', 'string'),
 ('AI1', 'string'),
 ('AL1', 'string'),
 ('AW6', 'string'),
 ('MW4', 'string'),
 ('AX6', 'string'),
 ('CV1', 'string'),
 ('ME1', 'string'),
 ('KC2', 'string'),
 ('CN1', 'string'),
 ('UA1', 'string'),
 ('GD5', 'string'),
 ('UG2', 'string'),
 ('AT3', 'string'),
 ('AT4', 'string'),
 ('GJ1', 'string'),
 ('MV1', 'string'),
 ('GA5', 'string'),
 ('CT2', 'string'),
 ('CG2', 'string'),
 ('ED1', 'string'),
 ('AE1', 'string'),
 ('CO1', 'string'),
 ('KE1', 'string'),
 ('KB1', 'string'),
 ('AI4', 'string'),
 ('MW3', 'string'),
 ('KG2', 'string'),
 ('AA2', 'string'),
 ('AX2', 'string'),
 ('AY1', 'string'),
 ('RH2', 'string'),
 ('OE2', 'string'),
 ('CU3', 'string'),
 ('MH1', 'string'),
 ('AM1', 'string'),
 ('AU4', 'string'),
 ('GA6', 'string'),
 ('KG1', 'string'),
 ('AU3', 'string'),
 ('AT7', 'string'),
 ('KD1', 'string'),
 ('GL1', 'string'),
 ('IA1', 'string'),
 ('GG2', 'string'),
 ('OD3', 'string'),
 ('UG1', 'string'),
 ('CB1', 'string'),
 ('AI6', 'string'),
 ('CI1', 'string'),
 ('CV2', 'string'),
 ('AZ2', 'string'),
 ('AD1', 'string'),
 ('AH1', 'string'),
 ('WD1', 'string'),
 ('AA4', 'string'),
 ('KC1', 'string'),
 ('IA2', 'string'),
 ('CF3', 'string'),
 ('AI2', 'string'),
 ('AT1', 'string'),
 ('GD4', 'string'),
 ('AX3', 'string'),
 ('AH4', 'string'),
 ('KB3', 'string'),
 ('CU1', 'string'),
 ('CN4', 'string'),
 ('AT2', 'string'),
 ('CG1', 'string'),
 ('CF1', 'string'),
 ('GG1', 'string'),
 ('MV2', 'string'),
 ('CW1', 'string'),
 ('GG4', 'string'),
 ('AB1', 'string'),
 ('AH5', 'string'),
 ('CN3', 'string')]

In [0]:
(df_weather.count(), len(df_weather.columns))

Out[16]: (29823926, 177)

In [0]:
display(df_weather)

STATION DATE SOURCE LATITUDE LONGITUDE ELEVATION NAME REPORT_TYPE CALL_SIGN QUALITY_CONTROL WND CIG VIS TMP DEW SLP AW1 GA1 GA2 GA3 GA4 GE1 GF1 KA1 KA2 MA1 MD1 MW1 MW2 OC1 OD1 OD2 REM EQD AW2 AX4 GD1 AW5 GN1 AJ1 AW3 MK1 KA4 GG3 AN1 RH1 AU5 HL1 OB1 AT8 AW7 AZ1 CH1 RH3 GK1 IB1 AX1 CT1 AK1 CN2 OE1 MW5 AO1 KA3 AA3 CR1 CF2 KB2 GM1 AT5 AY2 MW6 MG1 AH6 AU2 GD2 AW4 MF1 AA1 AH2 AH3 OE3 AT6 AL2 AL3 AX5 IB2 AI3 CV3 WA1 GH1 KF1 CU2 CT3 SA1 AU1 KD2 AI5 GO1 GD3 CG3 AI1 AL1 AW6 MW4 AX6 CV1 ME1 KC2 CN1 UA1 GD5 UG2 AT3 AT4 GJ1 MV1 GA5 CT2 CG2 ED1 AE1 CO1 KE1 KB1 AI4 MW3 KG2 AA2 AX2 AY1 RH2 OE2 CU3 MH1 AM1 AU4 GA6 KG1 AU3 AT7 KD1 GL1 IA1 GG2 OD3 UG1 CB1 AI6 CI1 CV2 AZ2 AD1 AH1 WD1 AA4 KC1 IA2 CF3 AI2 AT1 GD4 AX3 AH4 KB3 CU1 CN4 AT2 CG1 CF1 GG1 MV2 CW1 GG4 AB1 AH5 CN3 3809099999 2015-01-01T00:00:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-12 99999 V020 200,1,N,0077,1 00240,1,C,N 008000,1,9,9 +0113,1 +0099,1 10306,1 01,1,+00180,1,07,1 05,1,+00240,1,07,1 08,1,+00360,1,07,1 9,AGL ,+99999,+99999 08,99,1,01,1,99,9,00180,1,99,9,99,9 99999,9,10213,1 3,1,002,1,+999,9 51,1 3,99,0144,1,999 4,99,0134,1,999 SYN10603809 11358 82015 10113 20099 30213 40306 53002 69901 75165 887// 333 81706 85708 88712 90710 91128 91026= 5,1,02,1 06,0000,2,1 6,1,02,1 3809099999 2015-01-01T00:50:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-15 99999 V020 210,1,N,0077,1 00183,1,C,N 008000,1,9,9 +0110,1 +0100,1 99999,9 02,1,+00122,1,99,9 04,1,+00183,1,99,9 08,1,+00305,1,99,9 9,AGL ,+99999,+99999 99,99,9,02,1,99,9,00122,1,99,9,99,9 10290,1,99999,9 51,1 MET079METAR EGDR 010050Z 21015KT 8000 -DZ FEW004 SCT006 OVC010 11/10 Q1029 YLO1= 3809099999 2015-01-01T01:00:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-12 99999 V020 210,1,N,0077,1 00300,1,9,N 008000,1,9,9 +0113,1 +0101,1 10300,1 01,1,+00120,1,07,1 03,1,+00180,1,07,1 08,1,+00300,1,07,1 9,AGL ,+99999,+99999 08,99,1,01,1,99,9,00120,1,99,9,99,9 99999,9,10206,1 8,1,004,1,+999,9 51,1 3,99,0134,1,999 SYN09403809 41258 82115 10113 20101 30206 40300 58004 75155 887// 333 81704 83706 88710 90710 91126= 5,1,02,1 5,1,02,1 3809099999 2015-01-01T01:50:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-15 99999 V020 200,1,N,0082,1 00244,1,9,N 008000,1,9,9 +0120,1 +0100,1 99999,9 04,1,+00183,1,99,9 07,1,+00244,1,99,9 08,1,+00305,1,99,9 9,AGL ,+99999,+99999 99,99,9,04,1,99,9,00183,1,99,9,99,9 10290,1,99999,9 05,1 0144,1 MET086METAR EGDR 010150Z 20016G28KT 8000 HZ SCT006 BKN008 OVC010 12/10 Q1029 REDZ YLO1= 3809099999 2015-01-01T02:00:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-12 99999 V020 200,1,N,0082,1 00240,1,C,N 008000,1,9,9 +0115,1 +0100,1 10294,1 03,1,+00180,1,07,1 05,1,+00240,1,07,1 08,1,+00300,1,07,1 9,AGL ,+99999,+99999 08,99,1,03,1,99,9,00180,1,99,9,99,9 99999,9,10201,1 8,1,008,1,+999,9 20,1 3,99,0149,1,999 4,99,0144,1,999 SYN10003809 41358 82016 10115 20100 30201 40294 58008 72052 886// 333 83706 85708 88710 90710 91129 91028= 2,1,02,1 5,1,02,1 3809099999 2015-01-01T02:50:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-15 99999 V020 210,1,N,0093,1 00122,1,9,N 006000,1,9,9 +0110,1 +0110,1 99999,9 02,1,+00061,1,99,9 07,1,+00122,1,99,9 08,1,+00213,1,99,9 9,AGL ,+99999,+99999 99,99,9,02,1,99,9,00061,1,99,9,99,9 10290,1,99999,9 51,1 MET079METAR EGDR 010250Z 21018KT 6000 -DZ FEW002 BKN004 OVC007 11/11 Q1029 YLO2= 3809099999 2015-01-01T03:00:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-12 99999 V020 210,1,N,0093,1 00120,1,C,N 006000,1,9,9 +0111,1 +0106,1 10296,1 01,1,+00060,1,07,1 05,1,+00120,1,07,1 08,1,+00210,1,07,1 9,AGL ,+99999,+99999 08,99,1,01,1,99,9,00060,1,99,9,99,9 99999,9,10203,1 5,1,010,1,+999,9 50,1 3,99,0144,1,999 SYN09403809 41156 82118 10111 20106 30203 40296 55010 75052 887// 333 81702 85704 88707 90710 91128= 2,1,02,1 5,1,02,1 3809099999 2015-01-01T03:50:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-15 99999 V020 200,1,N,0082,1 00122,1,9,N 006000,1,9,9 +0110,1 +0110,1 99999,9 02,1,+00061,1,99,9 07,1,+00122,1,99,9 08,1,+00183,1,99,9 9,AGL ,+99999,+

In [0]:
display(df_weather.select([(count(when(col(c).contains('None') | \
                            col(c).contains('NULL') | \
                            (col(c) == '' ) | \
                            col(c).isNull() | \
                            isnan(c), c 
                           ))/df_weather.count()).alias(c)
                    for c in df_weather.columns]))

STATION DATE SOURCE LATITUDE LONGITUDE ELEVATION NAME REPORT_TYPE CALL_SIGN QUALITY_CONTROL WND CIG VIS TMP DEW SLP AW1 GA1 GA2 GA3 GA4 GE1 GF1 KA1 KA2 MA1 MD1 MW1 MW2 OC1 OD1 OD2 REM EQD AW2 AX4 GD1 AW5 GN1 AJ1 AW3 MK1 KA4 GG3 AN1 RH1 AU5 HL1 OB1 AT8 AW7 AZ1 CH1 RH3 GK1 IB1 AX1 CT1 AK1 CN2 OE1 MW5 AO1 KA3 AA3 CR1 CF2 KB2 GM1 AT5 AY2 MW6 MG1 AH6 AU2 GD2 AW4 MF1 AA1 AH2 AH3 OE3 AT6 AL2 AL3 AX5 IB2 AI3 CV3 WA1 GH1 KF1 CU2 CT3 SA1 AU1 KD2 AI5 GO1 GD3 CG3 AI1 AL1 AW6 MW4 AX6 CV1 ME1 KC2 CN1 UA1 GD5 UG2 AT3 AT4 GJ1 MV1 GA5 CT2 CG2 ED1 AE1 CO1 KE1 KB1 AI4 MW3 KG2 AA2 AX2 AY1 RH2 OE2 CU3 MH1 AM1 AU4 GA6 KG1 AU3 AT7 KD1 GL1 IA1 GG2 OD3 UG1 CB1 AI6 CI1 CV2 AZ2 AD1 AH1 WD1 AA4 KC1 IA2 CF3 AI2 AT1 GD4 AX3 AH4 KB3 CU1 CN4 AT2 CG1 CF1 GG1 MV2 CW1 GG4 AB1 AH5 CN3 0.006434582822685941 0.0 0.14272952256385907 0.0 0.0 0.0 0.008559680140456986 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.0 0.9061935640048071 0.447685387878161 0.8165911876095562 0.9365228869656319 0.9985378025624445 0.593469268465203 0.41104999344090276 0.9115014769215758 0.9398797395481875 0.22899886668048328 0.7392663765799345 0.9187407522688571 0.9951165329954494 0.9273294505222266 0.9271331705009141 0.9801655373112261 0.1429248705642503 0.8954907555264494 0.985905101378873 0.9999891025246135 0.6492430314274408 0.9999962360693566 0.9994557893994055 0.9896826538664825 0.9983661673251066 0.9999006680779734 0.9981940302303495 0.9999998924591245 0.9986041015122057 0.9984876705909707 0.9999998386886867 0.9999986378155766 0.985848050944407 0.9999981897285953 0.9999999820765207 0.9839849231994149 0.8759505425965913 0.9984876705909707 0.9999863960792461 0.9999223196409124 0.9987953808828063 0.8600704116713108 0.999975677838652 0.9883392174024652 0.9966670752622487 0.9999994981425809 0.8600704116713108 0.9979793965662808 0.9968221671282351 0.9883392174024652 0.9883392174024652 0.9998836586961611 0.9994557893994055 0.9998691586014445 0.9649523928194312 1.0 0.9967134612265586 0.999909665664559 0.9887715675690344 0.9117533197285762 0.9995766115730579 0.9984964351723259 0.797141022239471 0.9999092892714946 0.9999093968123701 0.9967109160925044 0.9999650850624129 0.9999924900621925 1.0 0.9999992651373506 0.989584881287151 0.9999084827149282 0.9883392174024652 0.9988290949472833 0.989584881287151 0.9883392174024652 0.9883392174024652 0.8600704116713108 0.9994438165152637 0.9450152106710517 0.9998866339937174 0.9999085006384074 0.9994557893994055 0.9630726320856913 0.8600704116713108 0.9999084827149282 0.9975139417335291 0.9999997311478112 0.9999958596762922 0.999999928306083 0.9883392174024652 0.982568735333105 0.9998836766196404 0.9883392174024652 0.999574855072091 1.0 0.9999994264486639 0.998849868259739 0.9995645849184783 0.9999826679955612 0.9980541374747707 0.9999022811911062 0.8600704116713108 0.8600704116713108 0.9942054108510429 0.9998831747622213 0.8595681420121711 0.9998855227380036 0.9998836228492026 0.9999084827149282 0.9998792136733061 0.998492635394724 0.9704753516402914 0.9994372385983775 0.964418631607242 0.9984876705909707 0.9966675054257508 0.9883392174024652 0.9999013670936643 0.9999753552160255 0.999994425797952 0.999999085902558 0.998492635394724 0.999175591648225 0.9999910024134144 0.9998866339937174 1.0 0.9966899276982978 0.9999997490712904 0.9978238386898338 0.9999756419916935 0.8759505425965913 0.9999086798732 0.9896625616462386 0.9883392174024652 0.98612073875778 0.9998998077509692 0.9999092355010568 0.9999976878711763 0.9999991396729958 0.9998836049257234 0.9999326077180043 0.9900555339288863 0.9999084827149282 0.9965184716957524 0.998462523949577 0.9998797872246422 0.9999095402002042 0.9998836945431196 0.9883392174024652 0.9987543361153142 0.9976986969576812 0.8600704116713108 0.9883392174024652 0.9999975803303007 1.0 0.8600704116713108 1.0 0.9998870462337403 0.9999095939706419 0.9883392174024652

In [0]:
import pandas as pd

df1 = pd.read_csv("/dbfs/FileStore/shared_uploads/abajaj225@berkeley.edu/weather_6months_null_dataset_percentage.csv")
df1 = df1.T

In [0]:
#Saved the results of the above in weather_6months_null_dataset_percentage.csv
# The above cell to check for nulls took 5.87 hours to run.
import pandas as pd

df1 = pd.read_csv("/dbfs/FileStore/shared_uploads/abajaj225@berkeley.edu/weather_6months_null_dataset_percentage.csv")
df1 = df1.T

In [0]:
df1=df1.reset_index(drop=False).rename(columns={'index':'col_name',0:'null_percent'})
weather_6mon_ninety_percent_null_values = df1[df1['null_percent']>=0.9]['col_name'].values
weather_6mon_seventy_percent_null_values = df1[(df1['null_percent']>=0.7) & (df1['null_percent']<0.9) ]['col_name'].values
weather_6mon_seventy_percent_null_values

Out[20]: array(['GA2', 'MD1', 'EQD', 'CH1', 'CT1', 'AO1', 'AA1', 'CT3', 'CG3',
 'CT2', 'CG2', 'CO1', 'CB1', 'CG1', 'CW1'], dtype=object)

In [0]:
df1=df1.reset_index(drop=False).rename(columns={'index':'col_name',0:'null_percent'})

In [0]:
weather_6mon_ninety_percent_null_values = df1[df1['null_percent']>=0.9]['col_name'].values
weather_6mon_ninety_percent_null_values

Out[22]: array(['AW1', 'GA3', 'GA4', 'KA1', 'KA2', 'MW1', 'MW2', 'OC1', 'OD1',
 'OD2', 'AW2', 'AX4', 'AW5', 'GN1', 'AJ1', 'AW3', 'MK1', 'KA4',
 'GG3', 'AN1', 'RH1', 'AU5', 'HL1', 'OB1', 'AT8', 'AW7', 'AZ1',
 'RH3', 'GK1', 'IB1', 'AX1', 'AK1', 'CN2', 'OE1', 'MW5', 'KA3',
 'AA3', 'CR1', 'CF2', 'KB2', 'GM1', 'AT5', 'AY2', 'MW6', 'MG1',
 'AH6', 'AU2', 'GD2', 'AW4', 'MF1', 'AH2', 'AH3', 'OE3', 'AT6',
 'AL2', 'AL3', 'AX5', 'IB2', 'AI3', 'CV3', 'WA1', 'GH1', 'KF1',
 'CU2', 'SA1', 'AU1', 'KD2', 'AI5', 'GO1', 'GD3', 'AI1', 'AL1',
 'AW6', 'MW4', 'AX6', 'CV1', 'ME1', 'KC2', 'CN1', 'UA1', 'GD5',
 'UG2', 'AT3', 'AT4', 'GJ1', 'MV1', 'GA5', 'ED1', 'AE1', 'KE1',
 'KB1', 'AI4', 'MW3', 'KG2', 'AA2', 'AX2', 'AY1', 'RH2', 'OE2',
 'CU3', 'MH1', 'AM1', 'AU4', 'GA6', 'KG1', 'AU3', 'AT7', 'KD1',
 'GL1', 'IA1', 'GG2', 'OD3', 'UG1', 'AI6', 'CI1', 'CV2', 'AZ2',
 'AD1', 'AH1', 'WD1', 'AA4', 'KC1', 'IA2', 'CF3', 'AI2', 'AT1',
 'GD4', 'AX3', 'AH4', 'KB3', 'CU1', 'CN4', 'AT2', 'CF1', 'GG1',
 'MV2', 'GG4', 'AB1', 'AH5', 'CN3'], dtype=object)

In [0]:
df_weather = df_weather.drop(*weather_6mon_ninety_percent_null_values)
df_weather = df_weather.drop(*weather_6mon_seventy_percent_null_values)

In [0]:
weather_6mon_seventy_percent_null_values = df1[(df1['null_percent']>=0.7) & (df1['null_percent']<0.9) ]['col_name'].values
weather_6mon_seventy_percent_null_values

Out[25]: array(['GA2', 'MD1', 'EQD', 'CH1', 'CT1', 'AO1', 'AA1', 'CT3', 'CG3',
 'CT2', 'CG2', 'CO1', 'CB1', 'CG1', 'CW1'], dtype=object)

In [0]:
df_weather.count(),len(df_weather.columns)

Out[23]: (55792739, 22)

In [0]:
df_weather = df_weather.drop(*weather_6mon_ninety_percent_null_values)
df_weather = df_weather.drop(*weather_6mon_seventy_percent_null_values)

In [0]:
display(df_weather)

STATION DATE SOURCE LATITUDE LONGITUDE ELEVATION NAME REPORT_TYPE CALL_SIGN QUALITY_CONTROL WND CIG VIS TMP DEW SLP GA1 GE1 GF1 MA1 REM GD1 3809099999 2015-01-01T00:00:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-12 99999 V020 200,1,N,0077,1 00240,1,C,N 008000,1,9,9 +0113,1 +0099,1 10306,1 01,1,+00180,1,07,1 9,AGL ,+99999,+99999 08,99,1,01,1,99,9,00180,1,99,9,99,9 99999,9,10213,1 SYN10603809 11358 82015 10113 20099 30213 40306 53002 69901 75165 887// 333 81706 85708 88712 90710 91128 91026= 3809099999 2015-01-01T00:50:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-15 99999 V020 210,1,N,0077,1 00183,1,C,N 008000,1,9,9 +0110,1 +0100,1 99999,9 02,1,+00122,1,99,9 9,AGL ,+99999,+99999 99,99,9,02,1,99,9,00122,1,99,9,99,9 10290,1,99999,9 MET079METAR EGDR 010050Z 21015KT 8000 -DZ FEW004 SCT006 OVC010 11/10 Q1029 YLO1= 3809099999 2015-01-01T01:00:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-12 99999 V020 210,1,N,0077,1 00300,1,9,N 008000,1,9,9 +0113,1 +0101,1 10300,1 01,1,+00120,1,07,1 9,AGL ,+99999,+99999 08,99,1,01,1,99,9,00120,1,99,9,99,9 99999,9,10206,1 SYN09403809 41258 82115 10113 20101 30206 40300 58004 75155 887// 333 81704 83706 88710 90710 91126= 3809099999 2015-01-01T01:50:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-15 99999 V020 200,1,N,0082,1 00244,1,9,N 008000,1,9,9 +0120,1 +0100,1 99999,9 04,1,+00183,1,99,9 9,AGL ,+99999,+99999 99,99,9,04,1,99,9,00183,1,99,9,99,9 10290,1,99999,9 MET086METAR EGDR 010150Z 20016G28KT 8000 HZ SCT006 BKN008 OVC010 12/10 Q1029 REDZ YLO1= 3809099999 2015-01-01T02:00:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-12 99999 V020 200,1,N,0082,1 00240,1,C,N 008000,1,9,9 +0115,1 +0100,1 10294,1 03,1,+00180,1,07,1 9,AGL ,+99999,+99999 08,99,1,03,1,99,9,00180,1,99,9,99,9 99999,9,10201,1 SYN10003809 41358 82016 10115 20100 30201 40294 58008 72052 886// 333 83706 85708 88710 90710 91129 91028= 3809099999 2015-01-01T02:50:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-15 99999 V020 210,1,N,0093,1 00122,1,9,N 006000,1,9,9 +0110,1 +0110,1 99999,9 02,1,+00061,1,99,9 9,AGL ,+99999,+99999 99,99,9,02,1,99,9,00061,1,99,9,99,9 10290,1,99999,9 MET079METAR EGDR 010250Z 21018KT 6000 -DZ FEW002 BKN004 OVC007 11/11 Q1029 YLO2= 3809099999 2015-01-01T03:00:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-12 99999 V020 210,1,N,0093,1 00120,1,C,N 006000,1,9,9 +0111,1 +0106,1 10296,1 01,1,+00060,1,07,1 9,AGL ,+99999,+99999 08,99,1,01,1,99,9,00060,1,99,9,99,9 99999,9,10203,1 SYN09403809 41156 82118 10111 20106 30203 40296 55010 75052 887// 333 81702 85704 88707 90710 91128= 3809099999 2015-01-01T03:50:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-15 99999 V020 200,1,N,0082,1 00122,1,9,N 006000,1,9,9 +0110,1 +0110,1 99999,9 02,1,+00061,1,99,9 9,AGL ,+99999,+99999 99,99,9,02,1,99,9,00061,1,99,9,99,9 10280,1,99999,9 MET082METAR EGDR 010350Z 20016G26KT 6000 -DZ FEW002 BKN004 OVC006 11/11 Q1028 YLO2= 3809099999 2015-01-01T04:00:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-12 99999 V020 200,1,N,0082,1 00120,1,C,N 006000,1,9,9 +0113,1 +0107,1 10290,1 01,1,+00060,1,07,1 9,AGL ,+99999,+99999 08,99,1,01,1,99,9,00060,1,99,9,99,9 99999,9,10197,1 SYN10003809 41156 82016 10113 20107 30197 40290 57010 75152 887// 333 81702 85704 88706 90710 91127 91026= 3809099999 2015-01-01T04:50:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-15 99999 V020 200,1,N,0082,1 00122,1,9,N 002500,1,9,9 +0110,1 +0110,1 99999,9 04,1,+00061,1,99,9 9,AGL ,+99999,+99999 99,99,9,04,1,99,9,00061,1,99,9,99,9 10280,1,99999,9 MET076METAR EGDR 010450Z 20016G27KT 2500 -RADZ SCT002 OVC004 11/11 Q1028 AMB= 3809099999 2015-01-01T05:00:00.000+0000 4 50.086092 -5.255711 81.38 CULDROSE, UK FM-12 99999 V020 200,1,N,0082,1 00120,1,9,N 002500,1,9,9 +0114,1 +0109,1 10286,1 03,1,+00060,1,07,1 9,AGL ,+99999,+99999 08,99,1,03,1,99,9,00060,1,99,9,99,9 99999,9,10193,1 SYN09403809 41125 82016 10114 20109 30193 40286 58008 75865 887// 333 83702 88704 90710 91127 91027= 3809099999 2015-01-01T05

In [0]:
# df_weather = df_weather.withColumn("DATE", df_weather["DATE"].cast(StringType()))
# df_weather = df_weather.withColumn("STATION", df_weather["STATION"].cast(IntegerType()))

In [0]:
# display(df_weather)#.select(df_weather['STATION']))
df_weather.printSchema()

root
-- STATION: string (nullable = true)
-- DATE: timestamp (nullable = true)
-- SOURCE: short (nullable = true)
-- LATITUDE: double (nullable = true)
-- LONGITUDE: double (nullable = true)
-- ELEVATION: double (nullable = true)
-- NAME: string (nullable = true)
-- REPORT_TYPE: string (nullable = true)
-- CALL_SIGN: string (nullable = true)
-- QUALITY_CONTROL: string (nullable = true)
-- WND: string (nullable = true)
-- CIG: string (nullable = true)
-- VIS: string (nullable = true)
-- TMP: string (nullable = true)
-- DEW: string (nullable = true)
-- SLP: string (nullable = true)
-- GA1: string (nullable = true)
-- GE1: string (nullable = true)
-- GF1: string (nullable = true)
-- MA1: string (nullable = true)
-- REM: string (nullable = true)
-- GD1: string (nullable = true)

#### Loading stations data

In [0]:
df_stations = spark.read.parquet("/mnt/mids-w261/datasets_final_project/stations_data/*").cache()
display(df_stations)

usaf wban station_id lat lon neighbor_id neighbor_name neighbor_state neighbor_call neighbor_lat neighbor_lon distance_to_neighbor 690020 93218 69002093218 36.0 -121.233 69002093218 JOLON HUNTER LIGGETT MIL RES CA KHGT 36.0 -121.233 0.0 690020 93218 69002093218 36.0 -121.233 69007093217 FRITZSCHE AAF CA KOAR 36.683 -121.767 55.73024537916726 690020 93218 69002093218 36.0 -121.233 69014093101 EL TORO MCAS CA KNZJ 33.667 -117.733 255.49106220353934 690020 93218 69002093218 36.0 -121.233 70027127506 BARROW POINT BARROW AK KPBA 71.333 -156.65 2750.4353299559803 690020 93218 69002093218 36.0 -121.233 70045027512 LONELY AK LNI 70.917 -153.25 2676.3554370627153 690020 93218 69002093218 36.0 -121.233 70063027403 OLIKTOK POW 2 AK POLI 70.5 -149.883 2604.050248854232 690020 93218 69002093218 36.0 -121.233 70063526465 GALBRAITH LAKE AIRPORT AK PAGB 68.479 -149.49 2490.9756094472277 690020 93218 69002093218 36.0 -121.233 70063627405 PRUDHOE BAY AK PAUD 70.25 -148.333 2568.180281844432 690020 93218 69002093218 36.0 -121.233 70104626418 CENTRAL AIRPORT AK PACE 65.567 -144.765 2254.5584891291946 690020 93218 69002093218 36.0 -121.233 70119526625 SHISHMAREF/NEW AIRPORT AK PASH 66.25 -166.089 2743.6881828292408 690020 93218 69002093218 36.0 -121.233 70121326638 POINT LAY LIZ 2 AK PIZ 69.733 -163.017 2796.6187763021226 690020 93218 69002093218 36.0 -121.233 70148626642 KIVALINA AIRPORT AK PAVL 67.732 -164.548 2755.8847615355235 690020 93218 69002093218 36.0 -121.233 70162026508 UMIAT AK PAUM 69.367 -152.133 2580.421414177685 690020 93218 69002093218 36.0 -121.233 70171900490 SHUNGNAK AIRPORT AK PAGH 66.888 -157.162 2560.459862643483 690020 93218 69002093218 36.0 -121.233 70174526480 CHANDALAR LAKE AIRPORT AK PALR 67.511 -148.493 2423.3408124753164 690020 93218 69002093218 36.0 -121.233 70179326524 MANLEY HOT SPRINGS AK PAML 64.999 -150.638 2336.6091618691917 690020 93218 69002093218 36.0 -121.233 70199526628 CAPE DARBY REMOT COM OUTLT AK PAGL 64.55 -163.007 2610.7849480759573 690020 93218 69002093218 36.0 -121.233 70206026632 NORTHEAST CAPE AK KOHC 63.317 -168.967 2740.2899674712785 690020 93218 69002093218 36.0 -121.233 70222326602 KOYUK AIRPORT AK PAKK 64.935 -161.155 2576.6261990332778 690020 93218 69002093218 36.0 -121.233 70231226555 FAREWELL LAKE SEAPLANE BASE AK PAFK 62.543 -153.623 2293.7430034471354 690020 93218 69002093218 36.0 -121.233 70249526547 HAYES RIVER AIRPORT AK PAHZ 61.983 -152.083 2230.946084519868 690020 93218 69002093218 36.0 -121.233 70255026514 SKWENTNA AIRPORT AK PASW 61.977 -151.217 2209.0623964277706 690020 93218 69002093218 36.0 -121.233 70264026414 SUMMIT AK PAST 63.331 -149.127 2223.352307308065 690020 93218 69002093218 36.0 -121.233 70264726499 HEALY RIVER AIRPORT AK PAHV 63.866 -148.969 2246.1213363715397 690020 93218 69002093218 36.0 -121.233 70264846406 CANTWELL AIRPORT AK PATW 63.391 -148.956 2222.52653340686 690020 93218 69002093218 36.0 -121.233 70267526484 PAXSON AIRPORT AK PAXK 63.032 -145.498 2131.3748228756726 690020 93218 69002093218 36.0 -121.233 70269596402 JONESVILLE MINE AIRPORT AK PAJV 61.714 -148.909 2140.8509123873396 690020 93218 69002093218 36.0 -121.233 70271126439 SHEEP MOUNTAIN AIRPORT AK PASP 61.812 -147.507 2112.749500893187 690020 93218 69002093218 36.0 -121.233 70274526560 WILLOW AIRPORT AK PAUO 61.748 -150.054 2170.093644623675 690020 93218 69002093218 36.0 -121.233 70275026442 NATIONAL WEATHER SERVICE OFFI AK PAVW 61.13 -146.352 2052.4465612834106 690020 93218 69002093218 36.0 -121.233 70275546404 MCCARTHY AIRPORT AK PAMX 61.437 -142.904 1993.3299561949077 690020 93218 69002093218 36.0 -121.233 70275726444 WHITTIER AIRPORT AK PAWR 60.783 -148.733 2092.9535147837305 690020 93218 69002093218 36.0 -121.233 70291346402 DEVILS MOUNTAIN LODGE AIRPORT AK PABN 62.402 -142.995 2047.8132237563839 690020 93218 69002093218 36.0 -121.233 70291526486 DUFFY'S TAVERN AIRPORT AK PADT 62.709 -143.981 2083.812325469856 690020 93218 69002093218 36.0 -121.233 70292326440 TANACROSS AK TSG 63.383 -143.333 2

In [0]:
# Size of the dataframe

print(f"Size of the stations df: {df_stations.count(),len(df_stations.columns)}")
df_stations.printSchema()

Size of the stations df: (5004169, 12)
root
-- usaf: string (nullable = true)
-- wban: string (nullable = true)
-- station_id: string (nullable = true)
-- lat: double (nullable = true)
-- lon: double (nullable = true)
-- neighbor_id: string (nullable = true)
-- neighbor_name: string (nullable = true)
-- neighbor_state: string (nullable = true)
-- neighbor_call: string (nullable = true)
-- neighbor_lat: double (nullable = true)
-- neighbor_lon: double (nullable = true)
-- distance_to_neighbor: double (nullable = true)

In [0]:
# Count of distinct values in the dataframe
for col in df_stations.columns:
  print(f"Col {col} ,{df_stations.select(col).distinct().count()}")

Col usaf ,2227
Col wban ,2228
Col station_id ,2237
Col lat ,2028
Col lon ,2142
Col neighbor_id ,2237
Col neighbor_name ,2202
Col neighbor_state ,52
Col neighbor_call ,2229
Col neighbor_lat ,2028
Col neighbor_lon ,2142
Col distance_to_neighbor ,2474196

In [0]:
# Adding monotonically increasing ID to use as a key for a join
df_stations = df_stations.withColumn("id", monotonically_increasing_id())

In [0]:
['usaf',
 'wban',
 'station_id',
 'lat',
 'lon',
 'neighbor_id',
 'neighbor_name',
 'neighbor_state',
 'neighbor_call',
 'neighbor_lat',
 'neighbor_lon',
 'distance_to_neighbor']

Out[7]: ['usaf',
 'wban',
 'station_id',
 'lat',
 'lon',
 'neighbor_id',
 'neighbor_name',
 'neighbor_state',
 'neighbor_call',
 'neighbor_lat',
 'neighbor_lon',
 'distance_to_neighbor']

In [0]:
df_limited = df_stations.sort('id').limit(50)

In [0]:
df_limited.display()

usaf wban station_id lat lon neighbor_id neighbor_name neighbor_state neighbor_call neighbor_lat neighbor_lon distance_to_neighbor id 690020 93218 69002093218 36.0 -121.233 69002093218 JOLON HUNTER LIGGETT MIL RES CA KHGT 36.0 -121.233 0.0 0 690020 93218 69002093218 36.0 -121.233 69007093217 FRITZSCHE AAF CA KOAR 36.683 -121.767 55.73024537916726 1 690020 93218 69002093218 36.0 -121.233 69014093101 EL TORO MCAS CA KNZJ 33.667 -117.733 255.49106220353934 2 690020 93218 69002093218 36.0 -121.233 70027127506 BARROW POINT BARROW AK KPBA 71.333 -156.65 2750.4353299559803 3 690020 93218 69002093218 36.0 -121.233 70045027512 LONELY AK LNI 70.917 -153.25 2676.3554370627153 4 690020 93218 69002093218 36.0 -121.233 70063027403 OLIKTOK POW 2 AK POLI 70.5 -149.883 2604.050248854232 5 690020 93218 69002093218 36.0 -121.233 70063526465 GALBRAITH LAKE AIRPORT AK PAGB 68.479 -149.49 2490.9756094472277 6 690020 93218 69002093218 36.0 -121.233 70063627405 PRUDHOE BAY AK PAUD 70.25 -148.333 2568.180281844432 7 690020 93218 69002093218 36.0 -121.233 70104626418 CENTRAL AIRPORT AK PACE 65.567 -144.765 2254.5584891291946 8 690020 93218 69002093218 36.0 -121.233 70119526625 SHISHMAREF/NEW AIRPORT AK PASH 66.25 -166.089 2743.6881828292408 9 690020 93218 69002093218 36.0 -121.233 70121326638 POINT LAY LIZ 2 AK PIZ 69.733 -163.017 2796.6187763021226 10 690020 93218 69002093218 36.0 -121.233 70148626642 KIVALINA AIRPORT AK PAVL 67.732 -164.548 2755.8847615355235 11 690020 93218 69002093218 36.0 -121.233 70162026508 UMIAT AK PAUM 69.367 -152.133 2580.421414177685 12 690020 93218 69002093218 36.0 -121.233 70171900490 SHUNGNAK AIRPORT AK PAGH 66.888 -157.162 2560.459862643483 13 690020 93218 69002093218 36.0 -121.233 70174526480 CHANDALAR LAKE AIRPORT AK PALR 67.511 -148.493 2423.3408124753164 14 690020 93218 69002093218 36.0 -121.233 70179326524 MANLEY HOT SPRINGS AK PAML 64.999 -150.638 2336.6091618691917 15 690020 93218 69002093218 36.0 -121.233 70199526628 CAPE DARBY REMOT COM OUTLT AK PAGL 64.55 -163.007 2610.7849480759573 16 690020 93218 69002093218 36.0 -121.233 70206026632 NORTHEAST CAPE AK KOHC 63.317 -168.967 2740.2899674712785 17 690020 93218 69002093218 36.0 -121.233 70222326602 KOYUK AIRPORT AK PAKK 64.935 -161.155 2576.6261990332778 18 690020 93218 69002093218 36.0 -121.233 70231226555 FAREWELL LAKE SEAPLANE BASE AK PAFK 62.543 -153.623 2293.7430034471354 19 690020 93218 69002093218 36.0 -121.233 70249526547 HAYES RIVER AIRPORT AK PAHZ 61.983 -152.083 2230.946084519868 20 690020 93218 69002093218 36.0 -121.233 70255026514 SKWENTNA AIRPORT AK PASW 61.977 -151.217 2209.0623964277706 21 690020 93218 69002093218 36.0 -121.233 70264026414 SUMMIT AK PAST 63.331 -149.127 2223.352307308065 22 690020 93218 69002093218 36.0 -121.233 70264726499 HEALY RIVER AIRPORT AK PAHV 63.866 -148.969 2246.1213363715397 23 690020 93218 69002093218 36.0 -121.233 70264846406 CANTWELL AIRPORT AK PATW 63.391 -148.956 2222.52653340686 24 690020 93218 69002093218 36.0 -121.233 70267526484 PAXSON AIRPORT AK PAXK 63.032 -145.498 2131.3748228756726 25 690020 93218 69002093218 36.0 -121.233 70269596402 JONESVILLE MINE AIRPORT AK PAJV 61.714 -148.909 2140.8509123873396 26 690020 93218 69002093218 36.0 -121.233 70271126439 SHEEP MOUNTAIN AIRPORT AK PASP 61.812 -147.507 2112.749500893187 27 690020 93218 69002093218 36.0 -121.233 70274526560 WILLOW AIRPORT AK PAUO 61.748 -150.054 2170.093644623675 28 690020 93218 69002093218 36.0 -121.233 70275026442 NATIONAL WEATHER SERVICE OFFI AK PAVW 61.13 -146.352 2052.4465612834106 29 690020 93218 69002093218 36.0 -121.233 70275546404 MCCARTHY AIRPORT AK PAMX 61.437 -142.904 1993.3299561949077 30 690020 93218 69002093218 36.0 -121.233 70275726444 WHITTIER AIRPORT AK PAWR 60.783 -148.733 2092.9535147837305 31 690020 93218 69002093218 36.0 -121.233 70291346402 DEVILS MOUNTAIN LODGE AIRPORT AK PABN 62.402 -142.995 2047.8132237563839 32 690020 93218 69002093218 36.0 -121.233 70291526486 DUFFY'S TAVERN AIRPORT AK PADT 62.709 -143.981 2083.812325

In [0]:
df_limited.groupBy('neighbor_call').agg(collect_list("distance_to_neighbor"),collect_list("station_id")).display()

neighbor_call collect_list(distance_to_neighbor) collect_list(station_id) KHGT List(0.0) List(69002093218) KOAR List(55.73024537916726) List(69002093218) KNZJ List(255.49106220353934) List(69002093218) KPBA List(2750.4353299559803) List(69002093218) LNI List(2676.3554370627153) List(69002093218) POLI List(2604.050248854232) List(69002093218) PAGB List(2490.9756094472277) List(69002093218) PAUD List(2568.180281844432) List(69002093218) PACE List(2254.5584891291946) List(69002093218) PASH List(2743.6881828292408) List(69002093218) PIZ List(2796.6187763021226) List(69002093218) PAVL List(2755.8847615355235) List(69002093218) PAUM List(2580.421414177685) List(69002093218) PAGH List(2560.459862643483) List(69002093218) PALR List(2423.3408124753164) List(69002093218) PAML List(2336.6091618691917) List(69002093218) PAGL List(2610.7849480759573) List(69002093218) KOHC List(2740.2899674712785) List(69002093218) PAKK List(2576.6261990332778) List(69002093218) PAFK List(2293.7430034471354) List(69002093218) PAHZ List(2230.946084519868) List(69002093218) PASW List(2209.0623964277706) List(69002093218) PAST List(2223.352307308065) List(69002093218) PAHV List(2246.1213363715397) List(69002093218) PATW List(2222.52653340686) List(69002093218) PAXK List(2131.3748228756726) List(69002093218) PAJV List(2140.8509123873396) List(69002093218) PASP List(2112.749500893187) List(69002093218) PAUO List(2170.093644623675) List(69002093218) PAVW List(2052.4465612834106) List(69002093218) PAMX List(1993.3299561949077) List(69002093218) PAWR List(2092.9535147837305) List(69002093218) PABN List(2047.8132237563839) List(69002093218) PADT List(2083.812325469856) List(69002093218) TSG List(2108.276136733581) List(69002093218) PALV List(2186.5708909123296) List(69002093218) PAHC List(2443.8545748450447) List(69002093218) PALJ List(2217.8715987073997) List(69002093218) KCSP List(1685.8502377101395) List(69002093218) PAEL List(1679.952675881082) List(69002093218) KCDE List(1507.4336449160385) List(69002093218) PAAP List(1531.968527894382) List(69002093218) KPML List(2287.279755425709) List(69002093218) KDFB List(2491.1102593697187) List(69002093218) K8S0 List(962.3313412705597) List(69002093218) KO54 List(340.249552011019) List(69002093218) K6V3 List(2173.2457650913725) List(69002093218) KIIY List(2167.0931703250553) List(69002093218) KLBR List(1488.5339268639061) List(69002093218) KRBO List(1487.3813846671642) List(69002093218)

In [0]:
aggregation_window = Window.partitionBy('neighbor_call')
df_stations.select([col for col in df_limited.columns]).withColumn('min_distance_to_neighbor', min('distance_to_neighbor').over(aggregation_window)).display()

usaf wban station_id lat lon neighbor_id neighbor_name neighbor_state neighbor_call neighbor_lat neighbor_lon distance_to_neighbor id min_distance_to_neighbor 690020 93218 69002093218 36.0 -121.233 72568124019 DOUGLAS WY 4DG 42.75 -105.383 963.5894820852895 141 0.0 690070 93217 69007093217 36.683 -121.767 72568124019 DOUGLAS WY 4DG 42.75 -105.383 963.5215012508319 2378 0.0 690140 93101 69014093101 33.667 -117.733 72568124019 DOUGLAS WY 4DG 42.75 -105.383 915.9045210361446 4615 0.0 700271 27506 70027127506 71.333 -156.65 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2609.9395099062467 6852 0.0 700450 27512 70045027512 70.917 -153.25 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2528.7971501122884 9089 0.0 700630 27403 70063027403 70.5 -149.883 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2447.127450961432 11326 0.0 700635 26465 70063526465 68.479 -149.49 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2376.6276947681213 13563 0.0 700636 27405 70063627405 70.25 -148.333 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2407.2938438813467 15800 0.0 701046 26418 70104626418 65.567 -144.765 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2173.8696617187784 18037 0.0 701195 26625 70119526625 66.25 -166.089 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2761.959511134992 20274 0.0 701213 26638 70121326638 69.733 -163.017 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2719.070982503175 22511 0.0 701486 26642 70148626642 67.732 -164.548 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2732.3751605129974 24748 0.0 701620 26508 70162026508 69.367 -152.133 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2461.689673240543 26985 0.0 701719 00490 70171900490 66.888 -157.162 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2528.1337578183666 29222 0.0 701745 26480 70174526480 67.511 -148.493 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2324.8099576847244 31459 0.0 701793 26524 70179326524 64.999 -150.638 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2314.5691476789816 33696 0.0 701995 26628 70199526628 64.55 -163.007 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2662.726702782431 35933 0.0 702060 26632 70206026632 63.317 -168.967 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2839.868335180776 38170 0.0 702223 26602 70222326602 64.935 -161.155 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2611.797383409464 40407 0.0 702312 26555 70231226555 62.543 -153.623 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2356.0015003811777 42644 0.0 702495 26547 70249526547 61.983 -152.083 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2299.1562028826 44881 0.0 702550 26514 70255026514 61.977 -151.217 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2271.766872001082 47118 0.0 702640 26414 70264026414 63.331 -149.127 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2234.361518444202 49355 0.0 702647 26499 70264726499 63.866 -148.969 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2241.761344965542 51592 0.0 702648 46406 70264846406 63.391 -148.956 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2230.6646949559295 53829 0.0 702675 26484 70267526484 63.032 -145.498 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2121.1917198908714 56066 0.0 702695 96402 70269596402 61.714 -148.909 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2194.447946435266 58303 0.0 702711 26439 70271126439 61.812 -147.507 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2152.6570820965762 60540 0.0 702745 26560 70274526560 61.748 -150.054 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2231.1372784934365 62777 0.0 702750 26442 70275026442 61.13 -146.352 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2101.8582842929586 65014 0.0 702755 46404 70275546404 61.437 -142.904 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2002.0524469670463 67251 0.0 702757 26444 70275726444 60.783 -148.733 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2171.534723996675 69488 0.0 702913 46402 70291346402 62.402 -142.995 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2031.2574755249864 71725 0.0 702915 26486 70291526486 62.709 -143.981 72568124019 DOUGLAS WY 4DG 42.75 -105.383 2068.5203951412254 73962 0.0 702923 26440 70292326440 63.383 -143.333 72568124019 DOUGLAS WY 4DG 

In [0]:
def get_neighbours_stations(stations,distance):
  